In [1]:
import pandas as pd
import os


In [2]:
!pip install category_encoders==2.*


In [4]:
!pip install pandas-profiling==2.*

In [3]:
sample_submission=pd.read_csv('sample_submission.csv')
print(sample_submission.shape)
sample_submission.tail(2)


(60980, 29)


id  F1  F2  F3  F4  F5  F6  F7  F8  F9  ...  \
60978  FOODS_3_826_WI_3_evaluation   0   0   0   0   0   0   0   0   0  ...   
60979  FOODS_3_827_WI_3_evaluation   0   0   0   0   0   0   0   0   0  ...   

       F19  F20  F21  F22  F23  F24  F25  F26  F27  F28  
60978    0    0    0    0    0    0    0    0    0    0  
60979    0    0    0    0    0    0    0    0    0    0  

[2 rows x 29 columns]

In [5]:
sales_train=pd.read_csv('sales_train_validation.csv')
print(sales_train.shape)
sales_train.head()

(30490, 1919)


id        item_id    dept_id   cat_id store_id  \
0  HOBBIES_1_001_CA_1_validation  HOBBIES_1_001  HOBBIES_1  HOBBIES     CA_1   
1  HOBBIES_1_002_CA_1_validation  HOBBIES_1_002  HOBBIES_1  HOBBIES     CA_1   
2  HOBBIES_1_003_CA_1_validation  HOBBIES_1_003  HOBBIES_1  HOBBIES     CA_1   
3  HOBBIES_1_004_CA_1_validation  HOBBIES_1_004  HOBBIES_1  HOBBIES     CA_1   
4  HOBBIES_1_005_CA_1_validation  HOBBIES_1_005  HOBBIES_1  HOBBIES     CA_1   

  state_id  d_1  d_2  d_3  d_4  ...  d_1904  d_1905  d_1906  d_1907  d_1908  \
0       CA    0    0    0    0  ...       1       3       0       1       1   
1       CA    0    0    0    0  ...       0       0       0       0       0   
2       CA    0    0    0    0  ...       2       1       2       1       1   
3       CA    0    0    0    0  ...       1       0       5       4       1   
4       CA    0    0    0    0  ...       2       1       1       0       1   

   d_1909  d_1910  d_1911  d_1912  d_1913  
0       1       3       0       1       1  
1       1       0       0       0       0  
2       1       0       1       1       1  
3       0       1       3       7       2  
4       1       2       2       2       4  

[5 rows x 1919 columns]

In [10]:
#Contains information about the dates on which the products are sold.

calendar=pd.read_csv('calendar.csv')
print(calendar.shape)
calendar.head()

(1969, 14)


date  wm_yr_wk    weekday  wday  month  year    d event_name_1  \
0  2011-01-29     11101   Saturday     1      1  2011  d_1          NaN   
1  2011-01-30     11101     Sunday     2      1  2011  d_2          NaN   
2  2011-01-31     11101     Monday     3      1  2011  d_3          NaN   
3  2011-02-01     11101    Tuesday     4      2  2011  d_4          NaN   
4  2011-02-02     11101  Wednesday     5      2  2011  d_5          NaN   

  event_type_1 event_name_2 event_type_2  snap_CA  snap_TX  snap_WI  
0          NaN          NaN          NaN        0        0        0  
1          NaN          NaN          NaN        0        0        0  
2          NaN          NaN          NaN        0        0        0  
3          NaN          NaN          NaN        1        1        0  
4          NaN          NaN          NaN        1        0        1

In [6]:
#Contains information about the price of the products sold per store and date.

sell_prices=pd.read_csv('sell_prices.csv')
print(sell_prices.shape)
sell_prices.head()

(6841121, 4)


store_id        item_id  wm_yr_wk  sell_price
0     CA_1  HOBBIES_1_001     11325        9.58
1     CA_1  HOBBIES_1_001     11326        9.58
2     CA_1  HOBBIES_1_001     11327        8.26
3     CA_1  HOBBIES_1_001     11328        8.26
4     CA_1  HOBBIES_1_001     11329        8.26

In [7]:
# Randomly sample 10% of your "sell_prices" dataframe

sell_sample = sell_prices.sample(frac=0.05, random_state=42)
sell_sample.shape


(342056, 4)

In [11]:
#Merge "sell_sample" and "calendar" on `wm_yr_wk`

sell_calendar=pd.merge(sell_sample, calendar, on=['wm_yr_wk'])
print(sell_calendar.shape)
sell_calendar.head(2)

(2386857, 17)


store_id      item_id  wm_yr_wk  sell_price        date   weekday  wday  \
0     TX_3  FOODS_3_295     11448         0.8  2014-12-27  Saturday     1   
1     TX_3  FOODS_3_295     11448         0.8  2014-12-28    Sunday     2   

   month  year       d event_name_1 event_type_1 event_name_2 event_type_2  \
0     12  2014  d_1429          NaN          NaN          NaN          NaN   
1     12  2014  d_1430          NaN          NaN          NaN          NaN   

   snap_CA  snap_TX  snap_WI  
0        0        0        0  
1        0        0        0

In [12]:
#Adding and "id" column in `sell_calendar`

sell_calendar['id']=sell_calendar['item_id']+'_'+sell_calendar['store_id']+'_validation'
sell_calendar.shape

(2386857, 18)

In [13]:
sale_train=pd.DataFrame(sales_train.loc[:,'id':'d_100'])
sale_train.shape

(30490, 106)

In [25]:
#Merge "sell_calendar" and "sales_train" on `id`

sales=pd.merge(sell_calendar,sale_train,  on=['id'])
print(sales.shape)
sales.head(2)

(2386857, 123)


store_id_x    item_id_x  wm_yr_wk  sell_price        date   weekday  wday  \
0       TX_3  FOODS_3_295     11448         0.8  2014-12-27  Saturday     1   
1       TX_3  FOODS_3_295     11448         0.8  2014-12-28    Sunday     2   

   month  year       d  ... d_91 d_92 d_93 d_94  d_95  d_96  d_97 d_98 d_99  \
0     12  2014  d_1429  ...    0    0    0    0     0     0     0    0    0   
1     12  2014  d_1430  ...    0    0    0    0     0     0     0    0    0   

  d_100  
0     0  
1     0  

[2 rows x 123 columns]

In [29]:
import csv

In [ ]:
sales.to_csv()

In [17]:
sales.nunique()

id              30425
item_id_x        3049
dept_id             7
cat_id              3
store_id_x         10
                ...  
event_name_2        4
event_type_2        2
snap_CA             2
snap_TX             2
snap_WI             2
Length: 123, dtype: int64

In [20]:
from pandas_profiling import ProfileReport
profile = ProfileReport(sales, minimal=True).to_notebook_iframe()
profile

C:\Users\J8015\anaconda3\lib\site-packages\IPython\core\display.py:701: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")
